In [1]:
# Notebook parameters. Values here are for development only and 
# will be overridden when running via snakemake and papermill.
cohort_id = "CD-NU_Gbadolite_gamb_2015_Q3"
# cohort_id = 'ML-2_Kati_colu_2014_Q3'
# cohort_id = 'CI-LG_Agneby-Tiassa_colu_2012'
cohorts_analysis = "20230223"
contigs = ['2RL', '3RL', 'X']
sample_sets = "3.0"
min_cohort_size = 20
max_cohort_size = 50
h12_calibration_contig = '3L'
use_gcs_cache = False
dask_scheduler = "threads"

In [2]:
# Parameters
min_cohort_size = 20
max_cohort_size = 50
sample_sets = ["3.0"]
contigs = ["2RL", "3RL", "X"]
cohorts_analysis = "20230223"
h12_calibration_contig = "3L"
h12_signal_detection_min_delta_aic = 1000
h12_signal_detection_min_stat_max = 0.1
h12_signal_detection_gflanks = [6]
use_gcs_cache = False
dask_scheduler = "single-threaded"
cohort_id = "GH-WP_Shama-Ahanta-East_colu_2012_Q3"


In [3]:
from IPython.display import Markdown, HTML
import malariagen_data
import numpy as np
import pandas as pd
from pyprojroot import here
import yaml
import dask
dask.config.set(scheduler=dask_scheduler);
from textwrap import dedent

import geopandas as gpd
import bokeh.layouts as bklay
import bokeh.plotting as bkplt
import bokeh.models as bkmod
import plotly.express as px

from bokeh.io import output_notebook # enables plot interface in J notebook

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Ghana / Shama Ahanta East / coluzzii / 2012 / Q3

In [4]:
# Load cohorts to find sample query to select samples for this cohort.

df_cohorts = gpd.read_file(here() / "build" / "final_cohorts.geojson").set_index("cohort_id")
cohort = df_cohorts.loc[cohort_id]
cohort

cohort_size                                                          24
country                                                           Ghana
admin1_iso                                                        GH-WP
admin1_name                                                     Western
admin2_name                                 Sekondi Takoradi Metropolis
taxon                                                          coluzzii
year                                                               2012
quarter                                                               3
cohort_label           Ghana / Shama Ahanta East / coluzzii / 2012 / Q3
sample_query          cohort_admin2_quarter == 'GH-WP_Shama-Ahanta-E...
latitude                                                          4.912
longitude                                                        -1.774
h12_window_size                                                  2000.0
country_alpha2                                                  

In [5]:
# Initialise access to MalariaGEN data.

extra_params = dict()
if use_gcs_cache:
    extra_params["url"] = "simplecache::gs://vo_agam_release"
    extra_params["simplecache"] = dict(cache_storage=(here() / "gcs_cache").as_posix())

ag3 = malariagen_data.Ag3(
    # Pin the version of the cohorts analysis for reproducibility.
    cohorts_analysis=cohorts_analysis,
    results_cache=(here() / "malariagen_data_cache").as_posix(),
    **extra_params,
)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8
Results cache           : /home/sanjaynagi/selection-atlas/malariagen_data_cache
Cohorts analysis        : 20230223
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 7.13.0
Client location         : unknown
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact data@malariagen.net. For API documentation see 
https://malariagen.github.io/vector-data/ag3/api.html

In [6]:
# Load sample metadata for this cohort.

df_samples = ag3.sample_metadata(sample_query=cohort['sample_query'])
df_samples

sample_id partner_sample_id    contributor country  location  year  month  \
0   AA0103-C       Takoradi_H9  David Weetman   Ghana  Takoradi  2012      8   
1   AA0115-C      Takoradi_A10  David Weetman   Ghana  Takoradi  2012      8   
2   AA0055-C       Takoradi_B9  David Weetman   Ghana  Takoradi  2012      8   
3   AA0116-C      Takoradi_F11  David Weetman   Ghana  Takoradi  2012      8   
4   AA0066-C       Takoradi_G7  David Weetman   Ghana  Takoradi  2012      8   
5   AA0104-C      Takoradi_E11  David Weetman   Ghana  Takoradi  2012      8   
6   AA0044-C      Takoradi_D10  David Weetman   Ghana  Takoradi  2012      8   
7   AA0042-C       Takoradi_C7  David Weetman   Ghana  Takoradi  2012      8   
8   AA0114-C       Takoradi_F8  David Weetman   Ghana  Takoradi  2012      8   
9   AA0126-C       Takoradi_G8  David Weetman   Ghana  Takoradi  2012      8   
10  AA0054-C       Takoradi_E7  David Weetman   Ghana  Takoradi  2012      8   
11  AA0128-C      Takoradi_H11  David Weetman   Ghana  Takoradi  2012      8   
12  AA0092-C      Takoradi_C11  David Weetman   Ghana  Takoradi  2012      8   
13  AA0043-C       Takoradi_H8  David Weetman   Ghana  Takoradi  2012      8   
14  AA0127-C      Takoradi_C10  David Weetman   Ghana  Takoradi  2012      8   
15  AA0090-C       Takoradi_D8  David Weetman   Ghana  Takoradi  2012      8   
16  AA0067-C       Takoradi_C9  David Weetman   Ghana  Takoradi  2012      8   
17  AA0102-C       Takoradi_E8  David Weetman   Ghana  Takoradi  2012      8   
18  AA0056-C      Takoradi_G10  David Weetman   Ghana  Takoradi  2012      8   
19  AA0068-C      Takoradi_H10  David Weetman   Ghana  Takoradi  2012      8   
20  AA0091-C       Takoradi_G9  David Weetman   Ghana  Takoradi  2012      8   
21  AA0079-C       Takoradi_F9  David Weetman   Ghana  Takoradi  2012      8   
22  AA0080-C      Takoradi_A11  David Weetman   Ghana  Takoradi  2012      8   
23  AA0136-C      Takoradi_A12  David Weetman   Ghana  Takoradi  2012      8   

    latitude  longitude sex_call  ... admin1_name admin1_iso  \
0      4.912     -1.774        F  ...     Western      GH-WP   
1      4.912     -1.774        F  ...     Western      GH-WP   
2      4.912     -1.774        F  ...     Western      GH-WP   
3      4.912     -1.774        F  ...     Western      GH-WP   
4      4.912     -1.774        F  ...     Western      GH-WP   
5      4.912     -1.774        F  ...     Western      GH-WP   
6      4.912     -1.774        F  ...     Western      GH-WP   
7      4.912     -1.774        F  ...     Western      GH-WP   
8      4.912     -1.774        F  ...     Western      GH-WP   
9      4.912     -1.774        F  ...     Western      GH-WP   
10     4.912     -1.774        F  ...     Western      GH-WP   
11     4.912     -1.774        F  ...     Western      GH-WP   
12     4.912     -1.774        F  ...     Western      GH-WP   
13     4.912     -1.774        F  ...     Western      GH-WP   
14     4.912     -1.774        F  ...     Western      GH-WP   
15     4.912     -1.774        F  ...     Western      GH-WP   
16     4.912     -1.774        F  ...     Western      GH-WP   
17     4.912     -1.774        F  ...     Western      GH-WP   
18     4.912     -1.774        F  ...     Western      GH-WP   
19     4.912     -1.774        F  ...     Western      GH-WP   
20     4.912     -1.774        F  ...     Western      GH-WP   
21     4.912     -1.774        F  ...     Western      GH-WP   
22     4.912     -1.774        F  ...     Western      GH-WP   
23     4.912     -1.774        F  ...     Western      GH-WP   

          admin2_name     taxon  cohort_admin1_year  cohort_admin1_month  \
0   Shama Ahanta East  coluzzii     GH-WP_colu_2012   GH-WP_colu_2012_08   
1   Shama Ahanta East  coluzzii     GH-WP_colu_2012   GH-WP_colu_2012_08   
2   Shama Ahanta East  coluzzii     GH-WP_colu_2012   GH-WP_colu_2012_08   
3   Shama Ahanta East  coluzzii     GH-WP_colu_2012   GH-WP_colu_2012_08   
4   Shama Ahanta East

In [7]:
# Determine collection dates.

df_collection_dates = (
    df_samples
    .groupby(["year", "month"])
    .size()
    .reset_index()
    .rename(columns={0: 'count'})
)
df_collection_dates

year  month  count
0  2012      8     24

In [8]:
# Determine first and last collection months.

min_month = df_collection_dates["month"].min()
max_month = df_collection_dates["month"].max()

if min_month < 0:
    start_month = end_month = None
else:
    start_month = pd.to_datetime(min_month, format="%m").month_name()
    end_month = pd.to_datetime(max_month, format="%m").month_name()
    
start_month, end_month

('August', 'August')

In [9]:
# Determine unique collection locations.

df_locations = df_samples[["location", "longitude", "latitude"]].drop_duplicates()
df_locations

location  longitude  latitude
0  Takoradi     -1.774     4.912

In [10]:
# Extract provenance information about the samples.

df_contributors = df_samples[["release", "sample_set", "contributor"]].drop_duplicates()
df_contributors["study"] = df_contributors.apply(
    lambda v: "Ag1000G" if v["sample_set"].startswith("AG1000G") else "TODO",
    axis="columns"
)
df_contributors["release"] = df_contributors["release"].apply(
    lambda v: f"Ag{v}"
)
df_contributors.rename(columns={
    "contributor": "Contributor",
    "study": "Study",
    "release": "Data release",
    "sample_set": "Sample set",
}, inplace=True)
df_contributors.set_index(["Contributor", "Study", "Data release"], inplace=True)
df_contributors

Sample set
Contributor   Study   Data release            
David Weetman Ag1000G Ag3.0         AG1000G-GH

In [11]:
# Build a paragraph with summary information about the samples in this cohort.

n_locations = len(df_locations)

summary_info = f"""This cohort comprises {cohort['cohort_size']:,} samples from the 
*{cohort['taxon']}* taxon, collected from {n_locations} locations within the administrative 
division of {cohort['admin2_name']}, {cohort['admin1_name']}, {cohort['country']}."""

if start_month and start_month == end_month:
    summary_info += f""" Collections were made in {start_month} {cohort['year']}."""
elif start_month:
    summary_info += f""" Collections were made between {start_month} and {end_month} in {cohort['year']}."""
else:
    summary_info += f""" Collections were made in {cohort['year']}."""
    
display(Markdown(summary_info))


This cohort comprises 24 samples from the 
*coluzzii* taxon, collected from 1 locations within the administrative 
division of Sekondi Takoradi Metropolis, Western, Ghana. Collections were made in August 2012.

## Selection scans

In [12]:
# load signals to overlay on H12 plots
import pandas as pd

df_signals_contigs = []
for contig in contigs:

    try:
        df_signals_contig = pd.read_csv(here() / "build/h12-signal-detection/" / f"{cohort_id}_{contig}.csv")
    except pd.errors.EmptyDataError:
        df_signals_contig = pd.DataFrame()
    df_signals_contigs.append(df_signals_contig)  
    
df_signals = pd.concat(df_signals_contigs)

# Add extra columns to help with overlaying signals on plots.
df_signals["bottom"] = 0
df_signals["top"] = 1

df_signals

cohort_id contig     gcenter   pcenter  delta_i  \
0  GH-WP_Shama-Ahanta-East_colu_2012_Q3    2RL   41.539831  20769916     1586   
1  GH-WP_Shama-Ahanta-East_colu_2012_Q3    2RL   81.884644  40942322     1887   
2  GH-WP_Shama-Ahanta-East_colu_2012_Q3    2RL  121.061946  64301605     1042   
3  GH-WP_Shama-Ahanta-East_colu_2012_Q3    2RL  166.408976  86975120     1434   
0  GH-WP_Shama-Ahanta-East_colu_2012_Q3    3RL   57.087225  28543613     2075   
0  GH-WP_Shama-Ahanta-East_colu_2012_Q3      X   30.574490  15287246     2591   

   stat_max    gpos_max  ppos_max  focus_gstart  focus_gstop  ...      skew  \
0  0.263021   41.569198  20784599     41.509408    41.582131  ... -0.237747   
1  0.460069   81.853372  40926686     81.776708    81.938612  ...  0.500000   
2  0.959201  120.600924  64071093    120.841540   121.310882  ... -0.087805   
3  0.599826  166.401062  86971162    166.387473   166.451981  ... -0.500000   
0  0.508681   57.080134  28540067     57.040132    57.166015  ... -0.371267   
0  0.733507   30.510972  15255486     30.193327    31.119687  ... -0.258185   

   decay_left  decay_right  baseline          aic          bic       rss  \
0    0.121691     0.169198  0.036780 -9378.929604 -9354.218820  0.118924   
1    0.431744     0.215872  0.041390 -6346.508857 -6322.999056  0.330543   
2    0.881624     0.995744  0.093406 -3497.024293 -3473.890704  7.254721   
3    0.086010     0.172021  0.070767 -6908.624882 -6884.187119  0.841753   
0    0.188369     0.315162  0.037282 -7547.334500 -7523.158577  0.275001   
0    1.524652     2.180789  0.041422 -5928.090487 -5903.745415  2.006442   

   constant_aic  bottom  top  
0  -7792.689818       0    1  
1  -4458.973659       0    1  
2  -2455.020623       0    1  
3  -5474.550491       0    1  
0  -5472.187163       0    1  
0  -3336.171101       0    1  

[6 rows x 32 columns]

In [13]:
# load window sizes 
h12_calibration_dir = "build/h12-calibration"
with open(here() / h12_calibration_dir / f"{cohort_id}.yaml") as h12_calibration_file:
    h12_calibration_params = yaml.safe_load(h12_calibration_file)
h12_window_size = h12_calibration_params["h12_window_size"]
g123_calibration_dir = "build/g123-calibration"
with open(here() / g123_calibration_dir / f"{cohort_id}.yaml") as g123_calibration_file:
    g123_calibration_params = yaml.safe_load(g123_calibration_file)
g123_window_size = g123_calibration_params["g123_window_size"]

if cohort.taxon == 'arabiensis':
    phasing_analysis = 'arab'
else:
    phasing_analysis = 'gamb_colu'

ihs_window_size = 100

def plot_h12_g123_ihs_tracks(
        contig, 
        df_signals,
        sizing_mode='stretch_width', 
        show=False, 
        width=800, 
        track_height=150,
        genes_height=90,
    ):

    sample_query = cohort["sample_query"]
    
    fig1 = ag3.plot_h12_gwss_track(
        contig=contig, 
        window_size=h12_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        show=show,
        width=width,
        height=track_height,
    )
    fig1.xaxis.visible = False
        
    if not df_signals.empty:
        df = df_signals.query("contig == @contig")
        center_xs = [np.array([row.pcenter, row.pcenter]) for idx, row in df.iterrows()]
        center_ys = [np.array([0, 1]) for idx, row in df.iterrows()]
        source = bkmod.ColumnDataSource(data={
            'cohort': df.cohort_id,
            'chromosome': df.contig,
            'score': df.delta_i.astype(int),
            'peak_start': df.span2_pstart,
            'peak_stop': df.span2_pstop,
            'focus_start': df.focus_pstart,
            'focus_stop': df.focus_pstop,    
            'center_xs': center_xs,
            'center_ys': center_ys,
            'bottom': df.bottom ,
            'top': df.top,
            })
        quad = fig1.quad(bottom='bottom', top='top', left='peak_start', right='peak_stop', 
              source=source, color="gray", alpha=.1, line_width=1)
        quad2 = fig1.quad(bottom='bottom', top='top', left='focus_start', right='focus_stop', 
              source=source, color="red", alpha=.4)
        glyph = bkmod.MultiLine(xs='center_xs', ys='center_ys', line_color='red', line_width=2, line_alpha=0.8)
        fig1.add_glyph(source, glyph)
    
        hover = bkmod.HoverTool(tooltips=[
            ("Cohort", '@cohort'),
            ("Score", '@score'),
            ("Focus", "@focus_start{,} - @focus_stop{,}"),
        ], renderers=[quad])

        fig1.add_tools(hover)
    
    fig2 = ag3.plot_g123_gwss_track(
        contig=contig, 
        window_size=g123_window_size, 
        sites=phasing_analysis,
        site_mask=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig2.xaxis.visible = False

    fig3 = ag3.plot_ihs_gwss_track(
        contig=contig, 
        window_size=ihs_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig3.xaxis.visible = False


    fig4 = ag3.plot_genes(
        region=contig, 
        show=show,
        sizing_mode=sizing_mode,
        width=width,
        height=genes_height,
        x_range=fig1.x_range
        )
                        
    fig = bklay.gridplot(
        [fig1, fig2, fig3, fig4],
        ncols=1,
        toolbar_location="above",
        merge_tools=True,
        sizing_mode=sizing_mode,
    )
    return fig 

In [14]:
for contig in contigs:
    
    display(HTML(f"<h3>Chromosome {contig}</h3>"))
    
    fig = plot_h12_g123_ihs_tracks(
        contig=contig,
        df_signals=df_signals,
    );

    bkplt.show(fig)


## Sampling information

In [15]:
from ipyleaflet import Map, Marker, basemaps
from ipywidgets import HTML

center = cohort[['latitude', 'longitude']].to_list()
m = Map(center=center, zoom=9, basemap=basemaps.OpenTopoMap)

df = df_samples[['latitude', 'longitude', 'taxon']].groupby(['latitude', 'longitude', 'taxon']).size().to_frame().rename(columns={0: 'count'}).reset_index()

for coh_id, row in df.iterrows():
    lat, long = row[['latitude', 'longitude']]
    
    if row['taxon'] == 'gambiae':
        color= 'red'
    elif row['taxon'] == 'coluzzii':
        color='cadetblue'
    elif row['taxon'] == 'arabiensis':
        color='lightgreen'
    else: 
        color='gray'

    marker = Marker(location=(lat, long), draggable=False, opacity=0.7, color=color)
    m.add_layer(marker);

    message2 = HTML()
    message2.value = f"n = {row['count']}"
    marker.popup = message2

display(m)

Map(center=[4.912, -1.774], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

In [16]:

if min_month >= 0:
    # For this cohort we have month data, so show a breakdown of sample
    # numbers by location and month.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.pivot_table(
        index=["location", "longitude", "latitude"],
        columns="month",
        values="sample_id",
        aggfunc="count",
        fill_value=0,
    )

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude")] + 
        [("Date", pd.to_datetime(x, format="%m").month_name()) 
         for x in df_loc_dt.columns[3:]], 
    )
    df_loc_dt.columns = cols
    
else:
    # For this cohort we do not have month data, so show a breakdown of sample
    # numbers by location only.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.groupby(["location", "longitude", "latitude"]).agg({"sample_id": "count"})

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude"), ("Date", cohort.year)]
    )
    df_loc_dt.columns = cols

# Style the table.
df_loc_dt_styled = (
    df_loc_dt
    .style
    .format(precision=3)
    .set_caption("Number of samples collected.")
    .hide()
)
display(df_loc_dt_styled)    

## Diagnostics
### H12 calibration

In [17]:
display(Markdown(f"Selected window size: **{h12_window_size:,}**"))

window_sizes = (100, 200, 500, 1000, 2000, 5000, 10000, 20000)

ag3.plot_h12_calibration(
    contig=h12_calibration_contig,
    analysis=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);


Selected window size: **2,000**

### G123 Calibration

In [18]:
display(Markdown(f"Selected window size: **{g123_window_size:,}**"))

ag3.plot_g123_calibration(
    contig=h12_calibration_contig,
    sites=phasing_analysis,
    site_mask=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);

Selected window size: **1,000**

## Data sources

In [19]:
df_sources_style = (
    df_contributors
    .style
    .set_caption("MalariaGEN Vector Observatory partners, studies and sample sets contributing data for this cohort.")
)
df_sources_style